In [1]:
import collections
import pickle
import random
from sklearn.metrics.pairwise import distance_metrics
import numpy as np
import torch
from torch.autograd import Variable
import torch.backends.cudnn as cudnn
import torch.nn as nn
import torch.optim as optim
import math
import torch.nn.functional as F
import torch.optim as optim
from numpy import linalg as LA

use_gpu = torch.cuda.is_available()

In [2]:
class SGC(nn.Module):
    """
    A Simple PyTorch Implementation of Logistic Regression.
    Assuming the features have been preprocessed with k-step graph propagation.
    """
    def __init__(self, nfeat, nclass):
        super(SGC, self).__init__()

        self.W = nn.Linear(nfeat, nclass)

    def forward(self, x):
        return self.W(x)
    
def get_model(model_opt, nfeat, nclass, cuda=True):
    if model_opt == "SGC":
        model = SGC(nfeat=nfeat,
                    nclass=nclass)
    else:
        raise NotImplementedError('model:{} is not implemented!'.format(model_opt))

    if cuda: model.cuda()
    return model

In [3]:
import easydict
np.random.seed(10)
args = easydict.EasyDict({
    'dataset': 'miniImagenet',
    'model': 'WideResNet28_10',
    'method': 'S2M2_R',
    'meta_val_way':5,
    'meta_val_query':15
})

In [4]:
def accuracy(output, labels):
    preds = output.max(1)[1].type_as(labels)
    correct = preds.eq(labels).double()
    correct = correct.sum()
    return correct / len(labels)

In [5]:
def save_pickle(file, data):
    with open(file, 'wb') as f:
        pickle.dump(data, f)

def load_pickle(file):
    with open(file, 'rb') as f:
        return pickle.load(f)

In [6]:
save_dir = 'checkpoints/miniImagenet/WideResNet28_10_S2M2_R_upload/last'
out_dict = load_pickle(save_dir + '/output.plk')

In [7]:
def sample_case(ld_dict, shot):
    sample_class = random.sample(list(ld_dict.keys()), args.meta_val_way)
    train_input = []
    test_input = []
    
    for each_class in sample_class:
        samples = random.sample(ld_dict[each_class], shot + args.meta_val_query)
        train_input += samples[:shot]
        test_input += samples[shot:]
    train_input = np.array(train_input).astype(np.float32)
    test_input = np.array(test_input).astype(np.float32)
    return train_input, test_input

In [8]:
def get_adj(train_data, test_data, k, alpha, kappa):
    eps = np.finfo(float).eps
    emb_all = np.append(train_data, test_data, axis=0)
    N = emb_all.shape[0]
    metric = distance_metrics()['cosine']
    S = 1 - metric(emb_all, emb_all)
    S = torch.tensor(S)
    S = S - torch.eye(S.shape[0])
    
    if k>0:
        topk, indices = torch.topk(S, k)
        mask = torch.zeros_like(S)
        mask = mask.scatter(1, indices, 1)
        mask = ((mask+torch.t(mask))>0).type(torch.float32)      
        S    = S*mask 
    
    D       = S.sum(0)
    Dnorm   = torch.diag(torch.pow(D, -0.5))
    E   = torch.matmul(Dnorm,torch.matmul(S, Dnorm))

    E = alpha * torch.eye(E.shape[0]) + E
    E = torch.matrix_power(E, kappa)
    
    E = E.cuda()
    train_data = train_data - train_data.mean(0)
    train_data_norm = train_data / LA.norm(train_data, 2, 1)[:, None]
    test_data = test_data - test_data.mean(0)
    test_data_norm = test_data / LA.norm(test_data, 2, 1)[:, None]
    features = np.append(train_data_norm, test_data_norm, axis=0)
    
    features = torch.tensor(features).cuda()
    return E, features

def get_labels(n_ways, shot, n_queries):
    train_labels = []
    test_labels = []
    classes = [i for i in range(n_ways)]
    for each_class in classes:
        train_labels += [each_class] * shot
        test_labels += [each_class] * n_queries

    train_labels = torch.tensor(train_labels).cuda()
    test_labels = torch.tensor(test_labels).cuda()
    return train_labels, test_labels

In [9]:
train_data, test_data = sample_case(out_dict, shot=1)
E, features = get_adj(train_data, test_data, k=15, alpha=0.2, kappa=1)
print(E)

tensor([[0.2000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.2000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
        [0.0000, 0.0000, 0.2000,  ..., 0.0000, 0.0000, 0.0000],
        ...,
        [0.0000, 0.0000, 0.0000,  ..., 0.2000, 0.0522, 0.0792],
        [0.0000, 0.0000, 0.0000,  ..., 0.0522, 0.2000, 0.0695],
        [0.0000, 0.0000, 0.0000,  ..., 0.0792, 0.0695, 0.2000]],
       device='cuda:0')


In [10]:
def sgc_precompute(features, E, degree):
    for i in range(degree):
        features = torch.spmm(E, features)
    
    return features

In [11]:
def compute_confidence_interval(data):
    """
    Compute 95% confidence interval
    :param data: An array of mean accuracy (or mAP) across a number of sampled episodes.
    :return: the 95% confidence interval for this data.
    """
    a = 1.0 * np.array(data)
    m = np.mean(a)
    std = np.std(a)
    pm = 1.96 * (std / np.sqrt(len(a)))
    return m, pm

def train_regression(model, features, train_labels, epochs=100, weight_decay=5e-6, lr=0.2):

    optimizer = optim.Adam(model.parameters(), lr=lr,
                           weight_decay=weight_decay)
    accs = []
    for epoch in range(epochs):
        model.train()
        optimizer.zero_grad()
        output = model(features)
        loss_train = F.cross_entropy(output, train_labels)
        loss_train.backward()
        optimizer.step()
        
    return model

def test_regression(model, features, test_labels):
    model.eval()
    output = model(features)
    return accuracy(output, test_labels)

In [12]:
def test_sgc(out_dict, shot, n_ways, n_queries, ite=10000, epochs=1000, degree=1, weight_decay=5e-6, lr=0.001):
    accs = {}
    alphas = [0.,0.25,0.5,0.75,1.]
    kappas = [1,2,3,4,5]
    for alpha in alphas:
        accs[alpha] = {}
        for kappa in kappas:
            accs[alpha][kappa] = []
    for i in range(ite):
        train_data, test_data = sample_case(out_dict, shot)
        train_labels, test_labels = get_labels(n_ways, shot, n_queries)
        for alpha in alphas:
            for kappa in kappas:
                E, features = get_adj(train_data, test_data, k=10, alpha=alpha, kappa=kappa)
                model_sgc = get_model(model_opt="SGC", nfeat=features.size(1), nclass=n_ways, cuda=True)
                features = sgc_precompute(features, E, degree)
                model_sgc = train_regression(model_sgc, features[:shot*n_ways,], train_labels, epochs=epochs, weight_decay=weight_decay, lr=lr)
                acc_test = test_regression(model_sgc, features[shot*n_ways:,], test_labels)
                accs[alpha][kappa].append(acc_test)
        print("\r("+str(i)+")",end='')
        liste = []
        for alpha in alphas:
            for kappa in kappas:
                accu = torch.stack(accs[alpha][kappa]).cpu().detach().numpy()
                acc_mean, acc_conf = compute_confidence_interval(accu)
                liste.append((alpha,kappa,acc_mean,acc_conf))
        liste.sort(key = lambda param: param[2], reverse=True)
        for i in range(len(liste)):
            print("({:f},{:d},{:4f},{:4f})".format(liste[i][0],liste[i][1],liste[i][2],liste[i][3]),end='')
test_sgc(out_dict=out_dict, shot=1, n_ways=args.meta_val_way, n_queries=args.meta_val_query)


(3879)(0.500000,3,0.761671,0.003827)(0.250000,2,0.761550,0.003795)(0.750000,4,0.761492,0.003842)(0.750000,3,0.761478,0.003776)(1.000000,4,0.761234,0.003800)(1.000000,3,0.760811,0.003718)(0.500000,2,0.760677,0.003713)(0.500000,4,0.760137,0.003895)(0.000000,2,0.760052,0.003859)(0.250000,3,0.759897,0.003873)(1.000000,5,0.759852,0.003865)(0.750000,2,0.758900,0.003646)(0.750000,5,0.758838,0.003927)(1.000000,2,0.756494,0.003588)(0.500000,5,0.756291,0.003958)(0.250000,4,0.754748,0.003919)(0.250000,1,0.754095,0.003621)(0.500000,1,0.750252,0.003539)(0.000000,1,0.749994,0.003798)(0.000000,3,0.747667,0.003935)(0.250000,5,0.746811,0.003965)(0.750000,1,0.744893,0.003480)(1.000000,1,0.739012,0.003452)(0.000000,4,0.734172,0.003953)(0.000000,5,0.716910,0.003975)(0.500000,3,0.760952,0.003952)(0.250000,2,0.760846,0.003918)(0.750000,3,0.760828,0.003898)(0.750000,4,0.760817,0.003965)(1.000000,4,0.760576,0.003920)(1.000000,3,0.760142,0.003834)(0.500000,2,0.760007,0.003831)(0.500000,4,0.759497,0.004021)(0.0

(3956)(0.500000,3,0.761558,0.003789)(0.250000,2,0.761433,0.003759)(0.750000,3,0.761342,0.003739)(0.750000,4,0.761335,0.003806)(1.000000,4,0.761072,0.003765)(1.000000,3,0.760674,0.003683)(0.500000,2,0.760593,0.003675)(0.000000,2,0.759919,0.003820)(0.500000,4,0.759912,0.003859)(0.250000,3,0.759734,0.003835)(1.000000,5,0.759676,0.003830)(0.750000,2,0.758735,0.003609)(0.750000,5,0.758678,0.003892)(1.000000,2,0.756345,0.003553)(0.500000,5,0.756045,0.003921)(0.250000,4,0.754564,0.003881)(0.250000,1,0.753896,0.003587)(0.500000,1,0.750029,0.003505)(0.000000,1,0.749907,0.003758)(0.000000,3,0.747520,0.003896)(0.250000,5,0.746562,0.003928)(0.750000,1,0.744701,0.003446)(1.000000,1,0.738918,0.003415)(0.000000,4,0.734041,0.003913)(0.000000,5,0.716776,0.003936)(0.500000,3,0.761524,0.003816)(0.250000,2,0.761401,0.003785)(0.750000,4,0.761356,0.003831)(0.750000,3,0.761315,0.003766)(1.000000,4,0.761096,0.003789)(1.000000,3,0.760682,0.003708)(0.500000,2,0.760534,0.003702)(0.500000,4,0.759986,0.003884)(0.0

(3970)(0.500000,3,0.761670,0.003784)(0.250000,2,0.761552,0.003753)(0.750000,3,0.761455,0.003734)(0.750000,4,0.761448,0.003800)(1.000000,4,0.761199,0.003760)(1.000000,3,0.760789,0.003679)(0.500000,2,0.760695,0.003671)(0.000000,2,0.760013,0.003813)(0.500000,4,0.760000,0.003853)(0.250000,3,0.759825,0.003829)(1.000000,5,0.759785,0.003824)(0.750000,2,0.758848,0.003606)(0.750000,5,0.758754,0.003886)(1.000000,2,0.756479,0.003549)(0.500000,5,0.756127,0.003917)(0.250000,4,0.754662,0.003876)(0.250000,1,0.754014,0.003583)(0.500000,1,0.750150,0.003501)(0.000000,1,0.750003,0.003752)(0.000000,3,0.747627,0.003891)(0.250000,5,0.746677,0.003923)(0.750000,1,0.744846,0.003444)(1.000000,1,0.739058,0.003413)(0.000000,4,0.734177,0.003909)(0.000000,5,0.716946,0.003932)(0.500000,3,0.761674,0.003788)(0.250000,2,0.761546,0.003757)(0.750000,3,0.761462,0.003738)(0.750000,4,0.761452,0.003804)(1.000000,4,0.761192,0.003763)(1.000000,3,0.760802,0.003682)(0.500000,2,0.760717,0.003674)(0.000000,2,0.760030,0.003818)(0.5

(3981)(0.500000,3,0.761699,0.003782)(0.250000,2,0.761574,0.003751)(0.750000,4,0.761480,0.003798)(0.750000,3,0.761477,0.003732)(1.000000,4,0.761232,0.003758)(1.000000,3,0.760812,0.003677)(0.500000,2,0.760718,0.003669)(0.000000,2,0.760050,0.003811)(0.500000,4,0.760030,0.003851)(0.250000,3,0.759859,0.003826)(1.000000,5,0.759819,0.003822)(0.750000,2,0.758865,0.003604)(0.750000,5,0.758788,0.003884)(1.000000,2,0.756502,0.003547)(0.500000,5,0.756163,0.003915)(0.250000,4,0.754703,0.003873)(0.250000,1,0.754018,0.003580)(0.500000,1,0.750164,0.003499)(0.000000,1,0.750017,0.003750)(0.000000,3,0.747657,0.003888)(0.250000,5,0.746710,0.003920)(0.750000,1,0.744864,0.003441)(1.000000,1,0.739077,0.003411)(0.000000,4,0.734189,0.003907)(0.000000,5,0.716959,0.003929)(0.500000,3,0.761675,0.003781)(0.250000,2,0.761554,0.003750)(0.750000,4,0.761456,0.003798)(0.750000,3,0.761456,0.003731)(1.000000,4,0.761208,0.003757)(1.000000,3,0.760792,0.003676)(0.500000,2,0.760698,0.003668)(0.000000,2,0.760030,0.003810)(0.5

(3992)(0.500000,3,0.761723,0.003773)(0.250000,2,0.761576,0.003742)(0.750000,4,0.761523,0.003792)(0.750000,3,0.761513,0.003726)(1.000000,4,0.761252,0.003752)(1.000000,3,0.760847,0.003671)(0.500000,2,0.760757,0.003663)(0.000000,2,0.760090,0.003804)(0.500000,4,0.760087,0.003845)(0.250000,3,0.759900,0.003820)(1.000000,5,0.759853,0.003815)(0.750000,2,0.758902,0.003598)(0.750000,5,0.758848,0.003877)(1.000000,2,0.756532,0.003542)(0.500000,5,0.756231,0.003908)(0.250000,4,0.754758,0.003867)(0.250000,1,0.754035,0.003575)(0.500000,1,0.750198,0.003493)(0.000000,1,0.750058,0.003743)(0.000000,3,0.747688,0.003882)(0.250000,5,0.746774,0.003913)(0.750000,1,0.744886,0.003435)(1.000000,1,0.739101,0.003405)(0.000000,4,0.734210,0.003900)(0.000000,5,0.716940,0.003922)(0.500000,3,0.761757,0.003775)(0.250000,2,0.761620,0.003744)(0.750000,4,0.761539,0.003791)(0.750000,3,0.761536,0.003725)(1.000000,4,0.761272,0.003751)(1.000000,3,0.760870,0.003670)(0.500000,2,0.760780,0.003662)(0.000000,2,0.760110,0.003804)(0.5

...

(9965)(0.500000,3,0.763596,0.002357)(0.250000,2,0.763479,0.002335)(0.750000,3,0.763415,0.002320)(1.000000,4,0.762999,0.002348)(0.750000,4,0.762964,0.002376)(1.000000,3,0.762700,0.002290)(0.500000,2,0.762565,0.002285)(1.000000,5,0.761631,0.002390)(0.000000,2,0.761545,0.002379)(0.250000,3,0.761236,0.002386)(0.500000,4,0.761086,0.002407)(0.750000,2,0.760587,0.002246)(0.750000,5,0.760021,0.002423)(1.000000,2,0.757762,0.002219)(0.500000,5,0.757399,0.002445)(0.250000,4,0.755633,0.002421)(0.250000,1,0.755232,0.002236)(0.000000,1,0.751797,0.002328)(0.500000,1,0.750754,0.002190)(0.000000,3,0.748622,0.002424)(0.250000,5,0.747794,0.002446)(0.750000,1,0.745401,0.002159)(1.000000,1,0.739830,0.002142)(0.000000,4,0.734900,0.002438)(0.000000,5,0.717909,0.002454)(0.500000,3,0.763597,0.002357)(0.250000,2,0.763480,0.002335)(0.750000,3,0.763415,0.002320)(1.000000,4,0.762998,0.002347)(0.750000,4,0.762965,0.002376)(1.000000,3,0.762697,0.002290)(0.500000,2,0.762563,0.002284)(1.000000,5,0.761631,0.002390)(0.0

(9976)(0.500000,3,0.763679,0.002355)(0.250000,2,0.763560,0.002333)(0.750000,3,0.763494,0.002319)(1.000000,4,0.763071,0.002346)(0.750000,4,0.763038,0.002375)(1.000000,3,0.762776,0.002288)(0.500000,2,0.762643,0.002283)(1.000000,5,0.761696,0.002388)(0.000000,2,0.761631,0.002378)(0.250000,3,0.761323,0.002384)(0.500000,4,0.761169,0.002405)(0.750000,2,0.760666,0.002244)(0.750000,5,0.760096,0.002421)(1.000000,2,0.757837,0.002218)(0.500000,5,0.757473,0.002443)(0.250000,4,0.755703,0.002419)(0.250000,1,0.755311,0.002234)(0.000000,1,0.751876,0.002327)(0.500000,1,0.750826,0.002188)(0.000000,3,0.748692,0.002423)(0.250000,5,0.747856,0.002445)(0.750000,1,0.745468,0.002157)(1.000000,1,0.739898,0.002141)(0.000000,4,0.734960,0.002437)(0.000000,5,0.717948,0.002452)(0.500000,3,0.763658,0.002356)(0.250000,2,0.763538,0.002333)(0.750000,3,0.763475,0.002319)(1.000000,4,0.763052,0.002346)(0.750000,4,0.763016,0.002375)(1.000000,3,0.762757,0.002288)(0.500000,2,0.762626,0.002283)(1.000000,5,0.761676,0.002388)(0.0

(9987)(0.500000,3,0.763677,0.002354)(0.250000,2,0.763561,0.002332)(0.750000,3,0.763496,0.002317)(1.000000,4,0.763073,0.002344)(0.750000,4,0.763037,0.002373)(1.000000,3,0.762775,0.002287)(0.500000,2,0.762648,0.002281)(1.000000,5,0.761696,0.002387)(0.000000,2,0.761634,0.002376)(0.250000,3,0.761324,0.002383)(0.500000,4,0.761167,0.002404)(0.750000,2,0.760665,0.002243)(0.750000,5,0.760095,0.002420)(1.000000,2,0.757837,0.002216)(0.500000,5,0.757460,0.002443)(0.250000,4,0.755689,0.002418)(0.250000,1,0.755322,0.002233)(0.000000,1,0.751882,0.002325)(0.500000,1,0.750818,0.002187)(0.000000,3,0.748692,0.002422)(0.250000,5,0.747853,0.002444)(0.750000,1,0.745460,0.002156)(1.000000,1,0.739889,0.002139)(0.000000,4,0.734976,0.002435)(0.000000,5,0.717968,0.002451)(0.500000,3,0.763673,0.002354)(0.250000,2,0.763558,0.002331)(0.750000,3,0.763491,0.002317)(1.000000,4,0.763070,0.002344)(0.750000,4,0.763032,0.002373)(1.000000,3,0.762772,0.002286)(0.500000,2,0.762644,0.002281)(1.000000,5,0.761690,0.002386)(0.0

(9998)(0.500000,3,0.763675,0.002353)(0.250000,2,0.763555,0.002331)(0.750000,3,0.763489,0.002316)(1.000000,4,0.763071,0.002343)(0.750000,4,0.763037,0.002372)(1.000000,3,0.762775,0.002286)(0.500000,2,0.762642,0.002280)(1.000000,5,0.761697,0.002385)(0.000000,2,0.761624,0.002375)(0.250000,3,0.761317,0.002382)(0.500000,4,0.761168,0.002402)(0.750000,2,0.760665,0.002242)(0.750000,5,0.760097,0.002419)(1.000000,2,0.757838,0.002215)(0.500000,5,0.757459,0.002441)(0.250000,4,0.755678,0.002417)(0.250000,1,0.755316,0.002232)(0.000000,1,0.751886,0.002324)(0.500000,1,0.750809,0.002186)(0.000000,3,0.748680,0.002421)(0.250000,5,0.747839,0.002443)(0.750000,1,0.745440,0.002155)(1.000000,1,0.739869,0.002139)(0.000000,4,0.734950,0.002435)(0.000000,5,0.717924,0.002451)(0.500000,3,0.763680,0.002353)(0.250000,2,0.763557,0.002331)(0.750000,3,0.763493,0.002316)(1.000000,4,0.763075,0.002343)(0.750000,4,0.763040,0.002372)(1.000000,3,0.762780,0.002285)(0.500000,2,0.762645,0.002280)(1.000000,5,0.761696,0.002385)(0.0

(9999)(0.500000,3,0.763704,0.002351)(0.250000,2,0.763579,0.002329)(0.750000,3,0.763529,0.002314)(1.000000,4,0.763115,0.002341)(0.750000,4,0.763060,0.002370)(1.000000,3,0.762816,0.002284)(0.500000,2,0.762683,0.002279)(1.000000,5,0.761721,0.002383)(0.000000,2,0.761644,0.002373)(0.250000,3,0.761333,0.002380)(0.500000,4,0.761180,0.002400)(0.750000,2,0.760709,0.002240)(0.750000,5,0.760121,0.002417)(1.000000,2,0.757879,0.002214)(0.500000,5,0.757471,0.002439)(0.250000,4,0.755695,0.002415)(0.250000,1,0.755363,0.002230)(0.000000,1,0.751901,0.002323)(0.500000,1,0.750859,0.002185)(0.000000,3,0.748704,0.002419)(0.250000,5,0.747853,0.002441)(0.750000,1,0.745487,0.002154)(1.000000,1,0.739916,0.002137)(0.000000,4,0.734963,0.002433)(0.000000,5,0.717944,0.002449)